### Load required libraries

In [1]:
%pip install gadm hdx-python-api
%pip install geopandas --upgrade
%pip install chart_studio

  Using cached gadm-0.0.5-py3-none-any.whl.metadata (3.2 kB)
  Using cached typing_extensions-4.12.2-py3-none-any.whl.metadata (3.0 kB)
  Using cached types_requests-2.32.0.20241016-py3-none-any.whl.metadata (1.9 kB)
  Using cached types_setuptools-75.6.0.20241126-py3-none-any.whl.metadata (2.0 kB)
  Using cached pycountry-22.3.5-py2.py3-none-any.whl
  Using cached geopandas-0.9.0-py2.py3-none-any.whl.metadata (908 bytes)
  Using cached fake_useragent-1.3.0-py3-none-any.whl.metadata (13 kB)
  Using cached requests-2.32.3-py3-none-any.whl.metadata (4.6 kB)
  Using cached tqdm-4.64.1-py2.py3-none-any.whl.metadata (57 kB)
  Using cached pandas-2.2.3-cp312-cp312-win_amd64.whl.metadata (19 kB)
  Using cached shapely-2.0.6-cp312-cp312-win_amd64.whl.metadata (7.2 kB)
  Using cached fiona-1.10.1-cp312-cp312-win_amd64.whl.metadata (58 kB)
  Using cached setuptools-75.6.0-py3-none-any.whl.metadata (6.7 kB)
  Using cached ckanapi-4.8-py3-none-any.whl.metadata (618 bytes)
  Using cached defopt-6.4

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gadm 0.0.5 requires geopandas==0.9.0, but you have geopandas 1.0.1 which is incompatible.



  Using cached plotly-5.24.1-py3-none-any.whl.metadata (7.3 kB)
  Using cached retrying-1.3.4-py3-none-any.whl.metadata (6.9 kB)
Using cached retrying-1.3.4-py3-none-any.whl (11 kB)
Using cached plotly-5.24.1-py3-none-any.whl (19.1 MB)


In [4]:
!pip install fiona --upgrade

In [6]:
!pip install folium

  Using cached folium-0.18.0-py2.py3-none-any.whl.metadata (3.8 kB)
  Using cached branca-0.8.0-py3-none-any.whl.metadata (1.5 kB)
  Using cached xyzservices-2024.9.0-py3-none-any.whl.metadata (4.1 kB)
Using cached folium-0.18.0-py2.py3-none-any.whl (108 kB)
Using cached branca-0.8.0-py3-none-any.whl (25 kB)
Using cached xyzservices-2024.9.0-py3-none-any.whl (85 kB)


In [7]:
import folium as fl
import pandas as pd
import geopandas as gpd
from hdx.api.configuration import Configuration
from hdx.data.resource import Resource
import json
import itertools
from shapely.geometry import Polygon,MultiPolygon
import time
import numpy as np
from gadm import GADMDownloader

c:\Users\vijay\Documents\Geospatial-Analysis\.venv\Lib\site-packages\quantulum3\classifier.py:28: UserWarning: Classifier dependencies not installed. Run pip install quantulum3[classifier] to install them. The classifer helps to dissambiguate units.
  warnings.warn(


### Load and preprocess India's population data (2022)

In [8]:
popdf = pd.read_csv('./ppp_IND_2020_1km_Aggregated_UNadj.csv')

In [9]:
popdf = popdf.reset_index()
popdf.head()

index          X          Y         Z
0      0  77.827916  35.503750  1.003104
1      1  77.836250  35.503750  0.977130
2      2  77.844583  35.503750  0.324360
3      3  77.819583  35.495417  0.826524
4      4  77.827916  35.495417  0.328031

In [10]:
popdf.columns = ['ID','xcoord','ycoord','population']
popdf['population'] = popdf['population'].astype(int)
pop = gpd.GeoDataFrame(popdf,geometry=gpd.points_from_xy(x=popdf.xcoord, y=popdf.ycoord))

In [11]:
print('Total Population:',round(pop['population'].sum()/1000000,2),'million')

Total Population: 1378.0 million


### Get country boundaries using GADM

In [12]:
# Initialize the GADMDownloader with the specified version (in this case, version 4.0)
downloader = GADMDownloader(version="4.0")

# Define the country name for which you want to retrieve administrative boundary data
country_name = "IND"

# Specify the administrative level you are interested in (e.g., 1 for districts or provinces)
ad_level = 2

# Retrieve the geospatial data for the selected country and administrative level
copygdf = downloader.get_shape_data_by_country_name(country_name=country_name, ad_level=ad_level)

In [13]:
copygdf

ID_0 COUNTRY               NAME_1 NL_NAME_1         ID_2  \
0    IND   India  Andaman and Nicobar              IND.1.1_1   
1    IND   India  Andaman and Nicobar              IND.1.2_1   
2    IND   India  Andaman and Nicobar              IND.1.3_1   
3    IND   India       Andhra Pradesh              IND.2.1_1   
4    IND   India       Andhra Pradesh              IND.2.2_1   
..   ...     ...                  ...       ...          ...   
661  IND   India          West Bengal            IND.36.16_1   
662  IND   India          West Bengal            IND.36.17_1   
663  IND   India          West Bengal            IND.36.18_1   
664  IND   India          West Bengal            IND.36.19_1   
665  IND   India          West Bengal            IND.36.20_1   

                       NAME_2             VARNAME_2 NL_NAME_2    TYPE_2  \
0             Nicobar Islands                                  District   
1    North and Middle Andaman                                  District   
2               South Andaman                                  District   
3                   Anantapur  Anantpur, Ananthapur            District   
4                    Chittoor       Chitoor|Chittor            District   
..                        ...                   ...       ...       ...   
661        Pashchim Medinipur     Paschim Medinipur            District   
662           Purba Medinipur       Purba Medinipur            District   
663                  Puruliya                                  District   
664         South 24 Parganas                                  District   
665            Uttar Dinajpur                                  District   

    ENGTYPE_2 CC_2    HASC_2  \
0    District       IN.AN.NI   
1    District       IN.AN.NM   
2    District       IN.AN.SA   
3    District       IN.AD.AN   
4    District       IN.AD.CH   
..        ...  ...       ...   
661  District       IN.WB.WM   
662  District       IN.WB.EM   
663  District       IN.WB.PU   
664  District       IN.WB.PS   
665  District       IN.WB.UD   

                                              geometry  
0    MULTIPOLYGON (((93.78988 6.85201, 93.79015 6.8...  
1    MULTIPOLYGON (((92.84441 12.14969, 92.84466 12...  
2    MULTIPOLYGON (((92.52111 10.89694, 92.52306 10...  
3    MULTIPOLYGON (((77.846 13.92832, 77.83012 13.9...  
4    MULTIPOLYGON (((78.54555 12.74391, 78.55031 12...  
..                                                 ...  
661  MULTIPOLYGON (((86.72535 22.2135, 86.73376 22....  
662  MULTIPOLYGON (((87.48177 21.60942, 87.48176 21...  
663  MULTIPOLYGON (((85.87758 23.47586, 85.89125 23...  
664  MULTIPOLYGON (((88.02139 21.57111, 88.02111 21...  
665  MULTIPOLYGON (((88.45433 25.663, 88.45429 25.6...  

[666 rows x 13 columns]

In [14]:
gdf = copygdf

### Select required state and region

In [15]:
region_name, state_name = 'Nadia', 'West Bengal'

In [16]:
gdf['NAME_1'].unique()

array(['Andaman and Nicobar', 'Andhra Pradesh', 'Arunachal Pradesh',
       'Assam', 'Bihar', 'Chandigarh', 'Chhattisgarh',
       'Dadra and Nagar Haveli', 'Daman and Diu', 'Goa', 'Gujarat',
       'Haryana', 'Himachal Pradesh', 'Jammu and Kashmir', 'Jharkhand',
       'Karnataka', 'Kerala', 'Lakshadweep', 'Madhya Pradesh',
       'Maharashtra', 'Manipur', 'Meghalaya', 'Mizoram', 'Nagaland',
       'NCT of Delhi', 'Odisha', 'Puducherry', 'Punjab', 'Rajasthan',
       'Sikkim', 'Tamil Nadu', 'Telangana', 'Tripura', 'Uttar Pradesh',
       'Uttarakhand', 'West Bengal'], dtype=object)

In [17]:
gdf = gdf[gdf['NAME_1'] == state_name]

In [18]:
gdf['NAME_2'].unique()

array(['Alipurduar', 'Bankura', 'Barddhaman', 'Birbhum',
       'Dakshin Dinajpur', 'Darjiling', 'Haora', 'Hugli', 'Jalpaiguri',
       'Koch Bihar', 'Kolkata', 'Maldah', 'Murshidabad', 'Nadia',
       'North 24 Parganas', 'Pashchim Medinipur', 'Purba Medinipur',
       'Puruliya', 'South 24 Parganas', 'Uttar Dinajpur'], dtype=object)

In [19]:
gdf = gdf[gdf['NAME_2'] == region_name]

In [20]:
selected_gdf = gdf

In [21]:
from IPython.display import display, HTML

display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 60% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 40% !important; /* Full height within the container */
        }
    </style>
"""))

m = fl.Map(zoom_start=1, tiles="OpenStreetMap")

bounds = selected_gdf.total_bounds 

m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

for _, r in selected_gdf.iterrows():

    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)

    geo_j = sim_geo.to_json()


    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "red"})


    fl.Popup(r["NAME_2"]).add_to(geo_j)


    geo_j.add_to(m)

display(HTML('<div class="map-container">' + m._repr_html_() + '</div>'))


### Population distribution in the area of interest

In [22]:
pop = pop.set_crs(selected_gdf.crs)

In [23]:
population_aoi = gpd.sjoin(pop, selected_gdf, predicate='within')
print(f'Total Population (Area of Interest - {selected_gdf}):',round(population_aoi['population'].sum()))

Total Population (Area of Interest -     ID_0 COUNTRY       NAME_1 NL_NAME_1         ID_2 NAME_2 VARNAME_2  \
659  IND   India  West Bengal            IND.36.14_1  Nadia             

    NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
659            District  District       IN.WB.NA   

                                              geometry  
659  MULTIPOLYGON (((88.40796 22.95147, 88.40676 22...  ): 5336589


In [24]:
quartile_labels = [0.1, 0.25, 0.5, 1.0]
population_aoi['opacity'] = pd.qcut(population_aoi['population'], 4, labels=quartile_labels)

In [25]:
print(population_aoi.head())

              ID     xcoord     ycoord  population                   geometry  \
1809166  1809166  88.711250  24.095417         530  POINT (88.71125 24.09542)   
1809167  1809167  88.719583  24.095417         528  POINT (88.71958 24.09542)   
1811836  1811836  88.686250  24.087083        1309  POINT (88.68625 24.08708)   
1811837  1811837  88.694583  24.087083        1223  POINT (88.69458 24.08708)   
1811838  1811838  88.702916  24.087083         176  POINT (88.70292 24.08708)   

         index_right ID_0 COUNTRY       NAME_1 NL_NAME_1         ID_2 NAME_2  \
1809166          659  IND   India  West Bengal            IND.36.14_1  Nadia   
1809167          659  IND   India  West Bengal            IND.36.14_1  Nadia   
1811836          659  IND   India  West Bengal            IND.36.14_1  Nadia   
1811837          659  IND   India  West Bengal            IND.36.14_1  Nadia   
1811838          659  IND   India  West Bengal            IND.36.14_1  Nadia   

        VARNAME_2 NL_NAME_2    T

In [26]:
print(population_aoi.describe())

                 ID       xcoord       ycoord    population  index_right
count  4.951000e+03  4951.000000  4951.000000   4951.000000       4951.0
mean   2.007059e+06    88.515552    23.475283   1077.881034        659.0
std    9.168621e+04     0.130554     0.290999    944.116718          0.0
min    1.809166e+06    88.136250    22.878750     19.000000        659.0
25%    1.938040e+06    88.427916    23.262083    634.000000        659.0
50%    2.009478e+06    88.527916    23.470417    829.000000        659.0
75%    2.074822e+06    88.619583    23.695417   1184.500000        659.0
max    2.190902e+06    88.794583    24.095417  18143.000000        659.0


### Show the population distribution in the area of interest

In [27]:
import folium as fl
import geopandas as gpd

m = fl.Map(zoom_start=12, tiles="OpenStreetMap")

bounds = selected_gdf.total_bounds 

m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

for _, r in selected_gdf.iterrows():

    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)

    geo_j = sim_geo.to_json()

    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "#ffffcc", "color": "black", "weight": 2, "fillOpacity": 0.3})


    geo_j.add_to(m)

import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

vmin = np.log1p(population_aoi['population'].min()+1) 
vmax = np.log1p(population_aoi['population'].max()) 

cmap = plt.get_cmap("OrRd") 
norm = mcolors.LogNorm(vmin=vmin, vmax=vmax)

for _, row in population_aoi.iterrows():

    coords = (row['ycoord'], row['xcoord']) 

    population_value = row['population']
    if population_value > 0:
        fill_color = mcolors.rgb2hex(cmap(norm(np.log1p(population_value)))[:3]) 
    else:
        fill_color = "#ffb68700" 

    fl.CircleMarker(
        location=coords,
        radius=2*max(2, np.log1p(population_value) / 5), 
        color=fill_color,
        fill=True,
        fill_opacity=0.7,
        opacity=0.4, 
        popup=f"Population: {population_value}" 
    ).add_to(m)
    
m

ModuleNotFoundError: No module named 'matplotlib'

### Get all hospital data in the AOI using Overpass API

In [28]:
import requests

overpass_url = "https://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
area["ISO3166-1"="IN"]["admin_level"="2"];
(node["amenity"="hospital"](area);
 way["amenity"="hospital"](area);
 rel["amenity"="hospital"](area);
);
out center;
"""
response = requests.get(overpass_url, params={'data': overpass_query})
data = response.json()

In [29]:
df_hospitals = pd.DataFrame(data['elements'])

df_hospitals['name'] = df_hospitals['tags'].apply(lambda x:x['name'] if 'name' in list(x.keys()) else None)

df_hospitals = df_hospitals[['id','lat','lon','name']].drop_duplicates()

df_health_osm = df_hospitals
df_health_osm = gpd.GeoDataFrame(df_health_osm, geometry=gpd.points_from_xy(df_health_osm.lon, df_health_osm.lat))
df_health_osm = df_health_osm[['id','name','geometry']]

print('Number of hospitals extracted:',len(df_health_osm))
df_health_osm = df_health_osm.set_crs(selected_gdf.crs)

Number of hospitals extracted: 49393


In [30]:
selected_hosp = gpd.sjoin(df_health_osm, selected_gdf, predicate='within')
print('Number of hospitals in AOI (',selected_gdf,'):',len(selected_hosp))

Number of hospitals in AOI (     ID_0 COUNTRY       NAME_1 NL_NAME_1         ID_2 NAME_2 VARNAME_2  \
659  IND   India  West Bengal            IND.36.14_1  Nadia             

    NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
659            District  District       IN.WB.NA   

                                              geometry  
659  MULTIPOLYGON (((88.40796 22.95147, 88.40676 22...   ): 51


In [31]:
selected_hosp.head(2)

id                               name  \
1972  3827017857  Kalyani Eye Care and Laser Clinic   
1973  3827017858                       Royal Vision   

                       geometry  index_right ID_0 COUNTRY       NAME_1  \
1972  POINT (88.46512 22.97077)          659  IND   India  West Bengal   
1973  POINT (88.46523 22.96871)          659  IND   India  West Bengal   

     NL_NAME_1         ID_2 NAME_2 VARNAME_2 NL_NAME_2    TYPE_2 ENGTYPE_2  \
1972            IND.36.14_1  Nadia                      District  District   
1973            IND.36.14_1  Nadia                      District  District   

     CC_2    HASC_2  
1972       IN.WB.NA  
1973       IN.WB.NA

In [32]:

for _, row in selected_hosp.iterrows():

    coords = (row.geometry.y, row.geometry.x) 

    hospital_name = row['name'] if row['name'] else "Unnamed Hospital"

    fl.CircleMarker(
        location=coords,
        radius=3, 
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.7,
        popup=hospital_name
    ).add_to(m)

m

### Get isochrone polygons using ORS API and calculate percentage of population access

In [35]:
ors_api_key = '5b3ce3597851110001cf62482253ee95a235474d85c4a81fedd541cd'

In [ ]:
def get_isochrone_osm (each_hosp):
  body = {"locations":[[each_hosp.x,each_hosp.y]],"range":[1800],"range_type":'time'}
  headers = {
      'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
      'Authorization': ors_api_key,
      'Content-Type': 'application/json; charset=utf-8'
  }
  call = requests.post('https://api.openrouteservice.org/v2/isochrones/driving-car', json=body, headers=headers)
  print(call.text)
  geom = (json.loads(call.text)['features'][0]['geometry'])
  polygon_geom = Polygon(geom['coordinates'][0])
  time.sleep(3)
  return polygon_geom

selected_hosp['cachment_area'] = selected_hosp['geometry'].apply(get_isochrone_osm)

{"type":"FeatureCollection","bbox":[88.210818,22.668405,88.672606,23.211902],"features":[{"type":"Feature","properties":{"group_index":0,"value":1800.0,"center":[88.4649912300066,22.970909876593584]},"geometry":{"coordinates":[[[88.210818,23.021657],[88.211555,23.02004],[88.215719,23.017116],[88.220095,23.015151],[88.221903,23.009204],[88.221584,23.007577],[88.224803,23.005963],[88.225307,23.006968],[88.22552,23.007422],[88.233043,23.011584],[88.23649,23.010545],[88.239253,23.002693],[88.238828,22.999118],[88.240316,22.996233],[88.24056,22.996105],[88.242384,22.996018],[88.248047,22.989404],[88.248114,22.988762],[88.248644,22.98785],[88.250908,22.985607],[88.257947,22.983573],[88.261204,22.98204],[88.261477,22.982621],[88.268369,22.985166],[88.271804,22.980195],[88.275463,22.973809],[88.267964,22.970234],[88.267893,22.970268],[88.267189,22.970099],[88.265498,22.968084],[88.265305,22.967321],[88.265229,22.967034],[88.26519,22.966287],[88.265744,22.965199],[88.267852,22.962655],[88.26900

In [37]:
def get_pop_count(cachment,pop_data):
  pop_access = pop_data[pop_data.within(cachment)]
  id_values = (pop_access['ID'].values)
  pop_with_access = (pop_access['population'].sum().round())
  return id_values,pop_with_access

selected_hosp['id_with_access'], selected_hosp['pop_with_access'] = zip(*selected_hosp['cachment_area'].apply(get_pop_count, pop_data=population_aoi))

In [38]:
list_ids_access = list(selected_hosp['id_with_access'].values)
list_ids_access = list(itertools.chain.from_iterable(list_ids_access))
pop_with_access = population_aoi[population_aoi['ID'].isin(list_ids_access)]
pop_without_access = population_aoi[~population_aoi['ID'].isin(list_ids_access)]

print('Population with Access:',round(pop_with_access['population'].sum()*100/population_aoi['population'].sum(),2),'%')

Population with Access: 85.25 %


In [39]:
from IPython.display import display, HTML
import folium as fl


display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 100% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 100% !important; /* Full height within the container */
        }
    </style>
"""))


folium_map = fl.Map(zoom_start=1, tiles="OpenStreetMap")


bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]


folium_map.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])


folium_map.get_root().html.add_child(fl.Element(f'<h3 style="text-align:center;"><b>Healthcare access distribution</b></h3>'))
folium_map.get_root().html.add_child(fl.Element(f'<h3 style="text-align:center;"><b>{region_name, state_name}</b></h3>'))


legend_html = """
<div style="position: fixed; 
            bottom: 50px; right: 50px; 
            background-color: white; 
            padding: 20px;
            border:2px solid grey;
            z-index:9999;">
    <b>Legend</b><br>
    <i style="color:red;font-size:20px;">&#9679;</i> Population with less access<br>
    <i style="color:green;font-size:20px;">&#9679;</i> Population with high access
</div>
"""
folium_map.get_root().html.add_child(fl.Element(legend_html))

geo_adm = fl.GeoJson(data=selected_gdf.iloc[0]['geometry'],style_function=lambda x:{'color': 'orange'})
geo_adm.add_to(folium_map)

for i in range(0,len(selected_hosp)):
    fl.Marker([selected_hosp.iloc[i]['geometry'].y, selected_hosp.iloc[i]['geometry'].x],
              popup=selected_hosp.iloc[i]['name']).add_to(folium_map)

# This loop is not necessary if pop_without_access is empty
for i in range(0,len(pop_without_access)):
  fl.CircleMarker(
        location=[pop_without_access.iloc[i]['ycoord'], pop_without_access.iloc[i]['xcoord']],
        radius=3,
        color=None,
        fill=True,
        fill_color='red',
        fill_opacity=pop_without_access.iloc[i]['opacity']).add_to(folium_map)

for i in range(0,len(pop_with_access)):
  fl.CircleMarker(
        location=[pop_with_access.iloc[i]['ycoord'], pop_with_access.iloc[i]['xcoord']],
        radius=3,
        color=None,
        fill=True,
        fill_color='green',
        fill_opacity=pop_with_access.iloc[i]['opacity']).add_to(folium_map)

folium_map

In [ ]:
folium_map.save(f'{region_name}_{state_name}_access.html')

In [40]:
def generate_grid_in_polygon(
    spacing: float, geometry: MultiPolygon
) -> gpd.GeoDataFrame:
    """
    This Function generates evenly spaced points within the given GeoDataFrame.
    The parameter 'spacing' defines the distance between the points in coordinate units.
    """

    # Get the bounds of the polygon
    minx, miny, maxx, maxy = geometry.bounds

    # Square around the country with the min, max polygon bounds
    # Now generate the entire grid
    x_coords = list(np.arange(np.floor(minx), int(np.ceil(maxx)), spacing))
    y_coords = list(np.arange(np.floor(miny), int(np.ceil(maxy)), spacing))
    mesh = np.meshgrid(x_coords, y_coords)
    grid = gpd.GeoDataFrame(
        data={"longitude": mesh[0].flatten(), "latitude": mesh[1].flatten()},
        geometry=gpd.points_from_xy(mesh[0].flatten(), mesh[1].flatten()),
        crs="EPSG:4326",
    )
    grid = gpd.clip(grid, geometry)
    grid = grid.reset_index(drop=True).reset_index().rename(columns={"index": "ID"})

    return grid

In [41]:
potential_locations = generate_grid_in_polygon(geometry=selected_gdf['geometry'].values[0],spacing=0.02)
len(potential_locations)

874

In [44]:
from IPython.display import display, HTML

display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 60% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 40% !important; /* Full height within the container */
        }
    </style>
"""))

folium_map = fl.Map(zoom_start=1, tiles="OpenStreetMap")

bounds = selected_gdf.total_bounds 

folium_map.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

geo_adm = fl.GeoJson(data=selected_gdf.iloc[0]['geometry'],style_function=lambda x:{'color': 'orange'})
geo_adm.add_to(folium_map)

for i in range(0,len(potential_locations)):
  fl.CircleMarker(
        location=[potential_locations.iloc[i]['latitude'], potential_locations.iloc[i]['longitude']],
        radius=2,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(folium_map)

folium_map

In [ ]:
# approximate positioning